<a href="https://colab.research.google.com/github/sokrypton/ColabDesign/blob/beta/af/examples/partial_hallucination_rewire.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Rewire

In [35]:
#@title install
%%bash
if [ ! -d params ]; then
  pip -q install git+https://github.com/sokrypton/af_backprop.git
  pip -q install git+https://github.com/sokrypton/ColabDesign.git@beta
  mkdir params
  curl -fsSL https://storage.googleapis.com/alphafold/alphafold_params_2021-07-14.tar | tar x -C params
fi

In [36]:
#@title import libraries
import os
from af import mk_design_model, clear_mem
from IPython.display import HTML
from google.colab import files
import numpy as np

#########################
def get_pdb(pdb_code=""):
  if pdb_code is None or pdb_code == "":
    upload_dict = files.upload()
    pdb_string = upload_dict[list(upload_dict.keys())[0]]
    with open("tmp.pdb","wb") as out: out.write(pdb_string)
    return "tmp.pdb"
  else:
    os.system(f"wget -qnc https://files.rcsb.org/view/{pdb_code}.pdb")
    return f"{pdb_code}.pdb"

# partial hallucination

In [37]:
old_pos = "4-9,13-26,30-33,37-50,54-59,63-76,80-84,112-125"

In [76]:
clear_mem()
model = mk_design_model(protocol="partial", use_templates=False)
model.prep_inputs(pdb_filename=get_pdb("2MR5"), chain="A",
                  pos=old_pos, length=100, fix_seq=False, sidechains=False)

In [138]:
seg_len = [b-a+1 for a,b in [[int(x) for x in r.split("-")] for r in old_pos.split(",")]]
new_order = [ 1,2,3,0,7,4,5,6]
loop_len =  [0,3,3,3,5,3,3,3,0]

l,new_pos = loop_len[0],[]
for n,i in enumerate(np.argsort(new_order)):
  new_pos.append(l + np.arange(seg_len[i]))
  l += seg_len[i] + loop_len[n+1]
  print(seg_len[i], loop_len[n+1])
new_pos = np.concatenate([new_pos[i] for i in new_order])

14 3
6 3
14 3
4 5
14 3
5 3
14 3
6 0


In [139]:
new_pos

array([17, 18, 19, 20, 21, 22, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36,
       37, 38, 39, 43, 44, 45, 46,  0,  1,  2,  3,  4,  5,  6,  7,  8,  9,
       10, 11, 12, 13, 94, 95, 96, 97, 98, 99, 52, 53, 54, 55, 56, 57, 58,
       59, 60, 61, 62, 63, 64, 65, 69, 70, 71, 72, 73, 77, 78, 79, 80, 81,
       82, 83, 84, 85, 86, 87, 88, 89, 90])

In [143]:
model.restart()
model.opt["pos"] = new_pos
model.opt["weights"].update({"dgram_cce":1.0,"con":0.1})
model.design_3stage(200,100,10)

1	model [4] soft 0.00 temp 1.00 loss 6.97 plddt 0.37 pae 0.72 con 8.03 dgram_cce 6.16 rmsd 55.99
2	model [2] soft 0.01 temp 1.00 loss 5.63 plddt 0.32 pae 0.57 con 6.31 dgram_cce 4.99 rmsd 47.88
3	model [3] soft 0.01 temp 1.00 loss 6.03 plddt 0.32 pae 0.64 con 6.41 dgram_cce 5.38 rmsd 29.10
4	model [3] soft 0.02 temp 1.00 loss 5.12 plddt 0.41 pae 0.72 con 5.80 dgram_cce 4.53 rmsd 24.08
5	model [2] soft 0.02 temp 1.00 loss 4.42 plddt 0.55 pae 0.67 con 4.89 dgram_cce 3.92 rmsd 22.15
6	model [4] soft 0.03 temp 1.00 loss 4.18 plddt 0.57 pae 0.64 con 4.32 dgram_cce 3.74 rmsd 17.44
7	model [1] soft 0.03 temp 1.00 loss 4.10 plddt 0.54 pae 0.63 con 4.04 dgram_cce 3.69 rmsd 18.65
8	model [2] soft 0.04 temp 1.00 loss 4.01 plddt 0.60 pae 0.64 con 4.18 dgram_cce 3.58 rmsd 21.04
9	model [2] soft 0.04 temp 1.00 loss 3.82 plddt 0.62 pae 0.61 con 3.88 dgram_cce 3.42 rmsd 19.23
10	model [4] soft 0.05 temp 1.00 loss 4.38 plddt 0.40 pae 0.60 con 4.65 dgram_cce 3.90 rmsd 25.23
11	model [4] soft 0.05 temp 1

In [145]:
HTML(model.animate(dpi=200))

In [144]:
model.save_pdb(f"{model.protocol}.pdb")
model.plot_pdb()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol